In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
from scipy.stats import pearsonr
from scipy.stats import spearmanr
import matplotlib.pyplot as plt

You should consider upgrading via the 'C:\Users\tripa\AppData\Local\Programs\Python\Python39\python.exe -m pip install --upgrade pip' command.


You should consider upgrading via the 'C:\Users\tripa\AppData\Local\Programs\Python\Python39\python.exe -m pip install --upgrade pip' command.


In [2]:
data = pd.read_csv("./../datasets/cleaned-datasets/PlotDataset.csv",low_memory=False)
data.head()

Year  AverageTemperature     City Latitude Longitude
0  1900              -0.989    Århus   57.05N    10.33E
1  1900               5.763    Çorlu   40.99N    27.69E
2  1900               0.947    Çorum   40.99N    34.08E
3  1900             -25.819  Öskemen   50.63N    82.39E
4  1900             -20.970   Ürümqi   44.20N    87.20E

In [3]:
grouped_multiple = data.groupby(['Year', 'City', 'Latitude','Longitude']).agg({'AverageTemperature': ['mean']})
grouped_multiple.columns = ['temp_mean']
grouped_multiple = grouped_multiple.reset_index()

In [4]:
grouped_multiple.to_csv('./../datasets/cleaned-datasets/YearwisePlotDataset.csv',index=False)

In [5]:
df = pd.read_csv("./../datasets/cleaned-datasets/TransformedYearwisePlotDataset.csv",low_memory=False)
df.head()

Year      City    Lat    Lon  temp_mean
0  1900  A Coruña  42.59  -8.73  13.267917
1  1900    Aachen  50.63   6.34   9.132500
2  1900   Aalborg  57.05  10.33   7.375250
3  1900       Aba   5.63   8.07  26.418833
4  1900    Abadan  29.74  48.00  25.016167

In [6]:
fig = px.scatter_geo(data_frame=df, color='temp_mean', hover_name='City', animation_frame='Year', lat='Lat', lon='Lon', projection='orthographic', color_continuous_scale='YlOrRd')
fig.update_layout(geo=dict(showframe=False, showocean=True, oceancolor='rgb(0,200,255)', lataxis=dict(showgrid = True, gridcolor = 'rgb(102, 102, 102)')))
fig.show()

In [7]:
data = pd.read_csv("./../datasets/raw-datasets/TransformedDatasetWithoutNA.csv")
data.head()
date = data['dt'].drop_duplicates().sort_values()
rough=np.NaN*(len(date))

In [8]:
data.loc[(data['Latitude'] > -10) & (data['Latitude'] < 10),'Region'] = '1.Equitorial'
data.loc[((data['Latitude'] > -20) & (data['Latitude'] <= -10)) | ((data['Latitude'] >= 10) & (data['Latitude'] < 20)),'Region'] = '2.Savanna'
data.loc[((data['Latitude'] > -30) & (data['Latitude'] <= -20)) | ((data['Latitude'] >= 20) & (data['Latitude'] < 30)),'Region'] = '3.Mid-Latitude Desert'
data.loc[((data['Latitude'] > -40) & (data['Latitude'] <= -30)) | ((data['Latitude'] >= 30) & (data['Latitude'] < 40)),'Region'] = '4.Mediterranean'
data.loc[((data['Latitude'] > -50) & (data['Latitude'] <= -40)) | ((data['Latitude'] >= 40) & (data['Latitude'] < 50)),'Region'] = '5.Temperate'
data.loc[((data['Latitude'] > -60) & (data['Latitude'] <= -50)) | ((data['Latitude'] >= 50) & (data['Latitude'] < 60)),'Region'] = '6.Continental'
data.loc[(data['Latitude'] <= -60) | (data['Latitude'] >= 60),'Region'] = '7.Tundra'

In [9]:
grouped_multiple = data.groupby(['dt', 'Region']).agg({'AverageTemperature': ['min', 'max', 'mean', 'median']})
grouped_multiple.columns = ['temp_min', 'temp_max', 'temp_mean', 'temp_median']
grouped_multiple = grouped_multiple.reset_index()

In [10]:
df = grouped_multiple
px.box(data_frame=df, x="Region", y="temp_mean", title="Regionwise Mean temperature range over 1900-2013")

In [11]:
px.box(data_frame=df, x="Region", y="temp_min", title="Regionwise Minimum temperature range over 1900-2013")

In [12]:
px.box(data_frame=df, x="Region", y="temp_max", title="Regionwise Maximum temperature range over 1900-2013")

In [13]:
px.box(data_frame=df, x="Region", y="temp_median", title="Regionwise Median temperature range over 1900-2013")

In [14]:
abc = df.filter(['dt','Region','temp_mean'], axis=1)
xyz=abc
xyz.set_index(['dt','Region'],inplace=True)
xyz=xyz.stack().unstack([1,2])
xyz.reset_index(inplace=True)
date=xyz["dt"]
equi=xyz["1.Equitorial"]["temp_mean"]
sav=xyz["2.Savanna"]["temp_mean"]
mid=xyz["3.Mid-Latitude Desert"]["temp_mean"]
med=xyz["4.Mediterranean"]["temp_mean"]
tem=xyz["5.Temperate"]["temp_mean"]
conti=xyz["6.Continental"]["temp_mean"]
tun=xyz["7.Tundra"]["temp_mean"]
date=date.to_numpy()
date = [i.split('-')[-1] for i in date] 
bardict = {
    'Date' : date,
    'Equitorial' : equi,
    'Savanna' : sav,
    'Mid-Latitude Desert' : mid,
    'Mediterranean' : med,
    'Temperate' : tem,
    'Continental' : conti,
    'Tundra' : tun
}
bar = pd.DataFrame(bardict)
bar2 = bar.groupby(['Date']).mean().reset_index()
bar2.to_csv('./../datasets/cleaned-datasets/BarTrain.csv',index=False)

In [15]:
forest = pd.read_csv("./../datasets/raw-datasets/forest.csv",low_memory=False)
forest.head()

Variable  COU    Country  Year    Value
0  Net fellings  AUS  Australia  1990  17295.0
1  Net fellings  AUS  Australia  1995  19560.0
2  Net fellings  AUS  Australia  2000  24407.0
3  Net fellings  AUS  Australia  2005  26998.0
4  Net fellings  AUS  Australia  2009  25624.0

In [16]:
forest2 = forest.groupby(['Country'])['Value'].sum().reset_index()

In [17]:
forest2

Country        Value
0         Australia   113884.000
1           Austria    87195.000
2           Belgium      270.151
3             Chile   220755.900
4          Colombia       26.081
5    Czech Republic   258843.000
6           Denmark    35503.436
7           Estonia   183192.427
8           Finland   922198.000
9            France   147570.048
10          Germany    94939.754
11           Greece      305.000
12          Hungary   155458.000
13          Ireland     4615.860
14            Italy    90338.276
15            Japan    10698.000
16            Korea    99998.000
17           Latvia   182171.655
18        Lithuania   155330.000
19       Luxembourg     6491.800
20      Netherlands     7473.000
21           Norway    67746.000
22           Poland   274781.000
23         Portugal   152372.072
24  Slovak Republic    85027.000
25         Slovenia    10213.926
26            Spain     6288.909
27           Sweden   402073.424
28      Switzerland    50121.539
29           Turkey    38530.000
30    United States  3941589.360

In [18]:
wildlife = pd.read_csv("./../datasets/raw-datasets/wildlife.csv",low_memory=False)
wildlife.head()
wildlife = wildlife[wildlife.IUCN_Category == 'Number of endangered indigenous species']
wildlife = wildlife.reset_index()
del wildlife['index']
del wildlife['IUCN_Category']
xyz = wildlife
xyz.set_index(['Country','Species'],inplace=True)
xyz=xyz.stack().unstack([1,2])
xyz.reset_index(inplace=True)
xyz

Species          Country Mammals Birds Reptiles Amphibians Vascular plants  \
                           Value Value    Value      Value           Value   
0              Australia    38.0  55.0     20.0       10.0           555.0   
1                Austria     6.0  24.0      3.0        3.0           348.0   
2                Belgium     2.0  15.0      2.0        3.0           107.0   
3                 Canada    10.0  14.0      6.0        5.0           325.0   
4                  Chile    13.0  25.0     18.0       23.0           199.0   
5               Colombia     3.0  20.0      NaN        NaN           175.0   
6         Czech Republic     1.0  35.0      3.0        3.0           412.0   
7                Denmark     2.0  15.0      NaN        4.0           101.0   
8                Estonia     1.0  31.0      1.0        2.0            67.0   
9                Finland     4.0  36.0      NaN        1.0            88.0   
10                France     NaN  30.0      NaN        NaN             NaN   
11               Germany    10.0  24.0      3.0        2.0           378.0   
12                Greece    13.0  17.0      2.0        2.0             NaN   
13               Hungary     3.0  20.0      4.0        1.0           162.0   
14               Ireland     NaN   NaN      0.0        1.0            25.0   
15                Israel    27.0  13.0      7.0        3.0           123.0   
16                 Korea     0.0   0.0      0.0        2.0            20.0   
17                Latvia     3.0  19.0      1.0        1.0           110.0   
18             Lithuania     3.0  17.0      1.0        1.0            66.0   
19            Luxembourg     NaN   NaN      NaN        NaN           124.0   
20                Mexico    20.0  51.0     18.0       13.0           130.0   
21           Netherlands     3.0  10.0      0.0        2.0           117.0   
22           New Zealand     2.0  13.0      8.0        0.0            64.0   
23                Norway     5.0  15.0      NaN        NaN           100.0   
24                Poland    10.0   8.0      1.0        NaN           140.0   
25              Portugal     7.0  30.0      4.0        NaN             NaN   
26       Slovak Republic     6.0  24.0      NaN        3.0             NaN   
27              Slovenia    19.0  43.0      7.0        3.0            80.0   
28                 Spain     6.0  21.0      5.0        2.0           202.0   
29                Sweden     3.0  11.0      NaN        0.0           114.0   
30           Switzerland    13.0  21.0      7.0        9.0           197.0   
31        United Kingdom     4.0  43.0      2.0        1.0           110.0   

Species Mosses Lichens Invertebrates  
         Value   Value         Value  
0          NaN     NaN          22.0  
1         69.0   135.0         310.0  
2          NaN     NaN         201.0  
3         85.0    51.0         295.0  
4          4.0     NaN          63.0  
5          1.0     0.0           NaN  
6         88.0   186.0        1173.0  
7         13.0    50.0         179.0  
8         24.0    74.0          43.0  
9         70.0    81.0         393.0  
10         NaN     NaN           NaN  
11       114.0   169.0        1010.0  
12         NaN     NaN           NaN  
13        90.0    44.0           7.0  
14         NaN     NaN          51.0  
15         NaN     NaN           NaN  
16         NaN     NaN          13.0  
17        41.0    18.0          38.0  
18        13.0    16.0          54.0  
19         NaN     NaN           NaN  
20         0.0     NaN          20.0  
21        27.0    42.0          60.0  
22         4.0     2.0          62.0  
23        61.0    73.0         459.0  
24        52.0   201.0         358.0  
25         NaN     NaN           NaN  
26         NaN     NaN           NaN  
27         NaN     NaN           NaN  
28        52.0     NaN          54.0  
29         NaN     NaN           NaN  
30        58.0    96.0         358.0  
31        37.0    34.0         118.0

In [19]:
result1 = pd.merge(xyz, forest2, how='inner', left_on = 'Country', right_on = 'Country')

C:\Users\tripa\AppData\Local\Temp/ipykernel_26048/3247294544.py:1: FutureWarning:

merging between different levels is deprecated and will be removed in a future version. (2 levels on the left,1 on the right)



In [20]:
result1.corr(method='pearson')['Value']

(Mammals, Value)           -0.130449
(Birds, Value)              0.190268
(Reptiles, Value)           0.128025
(Amphibians, Value)        -0.052378
(Vascular plants, Value)   -0.042646
(Mosses, Value)             0.218978
(Lichens, Value)            0.176176
(Invertebrates, Value)      0.197381
Value                       1.000000
Name: Value, dtype: float64

In [21]:
result1.corr(method='spearman')['Value']

(Mammals, Value)           -0.111995
(Birds, Value)              0.213570
(Reptiles, Value)           0.059321
(Amphibians, Value)        -0.225694
(Vascular plants, Value)    0.052372
(Mosses, Value)             0.288660
(Lichens, Value)            0.472527
(Invertebrates, Value)      0.078139
Value                       1.000000
Name: Value, dtype: float64

In [22]:
spearmanr(result1[('Birds', 'Value')], result1['Value'],nan_policy='omit')

SpearmanrResult(correlation=0.21357034772008127, pvalue=0.3053300912247075)

In [23]:
spearmanr(result1[('Mosses', 'Value')], result1['Value'],nan_policy='omit')

SpearmanrResult(correlation=0.288660106867137, pvalue=0.27824469326976997)

In [24]:
spearmanr(result1[('Lichens', 'Value')], result1['Value'],nan_policy='omit')

SpearmanrResult(correlation=0.47252747252747257, pvalue=0.0879674246125423)